In [1]:
import gensim 
import logging

logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

assert gensim.models.doc2vec.FAST_VERSION > -1 #ensure fast performance. Need to download C compiler, like MinGW

import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from sklearn.model_selection import KFold # import KFold
from sklearn import metrics
#import tensorflow as tf
#from tensorflow import keras

import csvWrite
import fileRetriever
import bagOfWords

#do plotting inline
%matplotlib inline

C:\Users\ga6198\AppData\Local\Continuum\anaconda3\lib\site-packages\smart_open\ssh.py:34: UserWarning: paramiko missing, opening SSH/SCP/SFTP paths will be disabled.  `pip install paramiko` to suppress
  warnings.warn('paramiko missing, opening SSH/SCP/SFTP paths will be disabled.  `pip install paramiko` to suppress')
C:\Users\ga6198\AppData\Local\Continuum\anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


## Get corpus

In [2]:
files = fileRetriever.getFileSet(2)
#corpus = bagOfWords.getTextList(files)


C:\VulnerabilityResearch\FileSet
C:\VulnerabilityResearch\julietFiles


In [3]:
corpus = []
for i, file in enumerate(files):
    wordList = []
    with open(file.dir, "r", encoding="utf8") as f:
        text = f.read()
        wordList = gensim.utils.simple_preprocess(text) #maybe add min_len and max_len params
        corpus.append(wordList)
        
    #if i == 0:
    #    print(wordList)
    
#may need to remove STOP WORDS here

In [4]:
corpus

[['php',
  'wpseo',
  'plugin',
  'file',
  'package',
  'wpseo',
  'admin',
  'bulk',
  'editor',
  'since',
  'implements',
  'table',
  'for',
  'bulk',
  'editing',
  'class',
  'extends',
  'wp_list_table',
  'the',
  'nonce',
  'that',
  'was',
  'passed',
  'with',
  'the',
  'request',
  'var',
  'string',
  'private',
  'nonce',
  'array',
  'of',
  'post',
  'types',
  'for',
  'which',
  'the',
  'current',
  'user',
  'has',
  'capabilities',
  'var',
  'array',
  'private',
  'all_posts',
  'array',
  'of',
  'post',
  'types',
  'for',
  'which',
  'the',
  'current',
  'user',
  'has',
  'edit_posts',
  'capabilities',
  'but',
  'not',
  'var',
  'array',
  'private',
  'own_posts',
  'saves',
  'all',
  'the',
  'metadata',
  'into',
  'this',
  'array',
  'var',
  'array',
  'protected',
  'meta_data',
  'array',
  'the',
  'current',
  'requested',
  'page_url',
  'var',
  'string',
  'private',
  'request_url',
  'the',
  'current',
  'page',
  'depending',
  'on',


In [5]:
print(type(corpus))

<class 'list'>


## Training the Word2Vec model

In [24]:
model = gensim.models.Word2Vec(corpus, size=150, window=10, min_count=5, workers=10)
model.train(corpus,total_examples=len(corpus),epochs=5)

2019-05-01 14:36:30,481 : WARNING : consider setting layer size to a multiple of 4 for greater performance
2019-05-01 14:36:30,482 : INFO : collecting all words and their counts
2019-05-01 14:36:30,483 : INFO : PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2019-05-01 14:36:30,732 : INFO : collected 13464 word types from a corpus of 2415675 raw words and 9709 sentences
2019-05-01 14:36:30,733 : INFO : Loading a fresh vocabulary
2019-05-01 14:36:30,805 : INFO : min_count=5 retains 5056 unique words (37% of original 13464, drops 8408)
2019-05-01 14:36:30,806 : INFO : min_count=5 leaves 2399715 word corpus (99% of original 2415675, drops 15960)
2019-05-01 14:36:30,816 : INFO : deleting the raw counts dictionary of 13464 items
2019-05-01 14:36:30,817 : INFO : sample=0.001 downsamples 130 most-common words
2019-05-01 14:36:30,817 : INFO : downsampling leaves estimated 1479386 word corpus (61.6% of prior 2399715)
2019-05-01 14:36:30,824 : INFO : estimated required memory f

2019-05-01 14:36:34,828 : INFO : worker thread finished; awaiting finish of 5 more threads
2019-05-01 14:36:34,828 : INFO : worker thread finished; awaiting finish of 4 more threads
2019-05-01 14:36:34,832 : INFO : worker thread finished; awaiting finish of 3 more threads
2019-05-01 14:36:34,832 : INFO : worker thread finished; awaiting finish of 2 more threads
2019-05-01 14:36:34,833 : INFO : worker thread finished; awaiting finish of 1 more threads
2019-05-01 14:36:34,833 : INFO : worker thread finished; awaiting finish of 0 more threads
2019-05-01 14:36:34,833 : INFO : EPOCH - 2 : training on 2415675 raw words (1467457 effective words) took 0.5s, 2672760 effective words/s
2019-05-01 14:36:35,378 : INFO : worker thread finished; awaiting finish of 9 more threads
2019-05-01 14:36:35,380 : INFO : worker thread finished; awaiting finish of 8 more threads
2019-05-01 14:36:35,381 : INFO : worker thread finished; awaiting finish of 7 more threads
2019-05-01 14:36:35,383 : INFO : worker thr

(7337195, 12078375)

## Analyze Output

In [25]:
#checking which words are most similar to an example word
w1 = "select"
model.wv.most_similar(positive=w1)

2019-05-01 14:36:38,129 : INFO : precomputing L2-norms of word weight vectors


[('tainted', 0.4343782961368561),
 ('where', 0.32410746812820435),
 ('employees', 0.2892302870750427),
 ('registration', 0.2569303512573242),
 ('temp', 0.2546007037162781),
 ('array', 0.2538211941719055),
 ('settype', 0.24165219068527222),
 ('handle', 0.2380194365978241),
 ('id', 0.23721152544021606),
 ('tag', 0.23433730006217957)]

In [26]:
w1 = "mysql_query"
model.wv.most_similar(positive=w1)

[('res', 0.44206055998802185),
 ('execution', 0.35313892364501953),
 ('while', 0.29132404923439026),
 ('br', 0.27570897340774536),
 ('query', 0.25239256024360657),
 ('usermenulib', 0.2359738051891327),
 ('islands', 0.23048235476016998),
 ('access', 0.21723482012748718),
 ('usermenu', 0.21092665195465088),
 ('print_r', 0.20488162338733673)]

In [27]:
w1 = "safe"
model.wv.most_similar(positive=w1)

[('php', 0.5152647495269775),
 ('unsafe', 0.4894552230834961),
 ('input', 0.44185709953308105),
 ('no_sanitizing', 0.3931344151496887),
 ('tainted', 0.37610724568367004),
 ('temp', 0.3638373017311096),
 ('public', 0.3289990723133087),
 ('set_sql_mode', 0.32339856028556824),
 ('return', 0.3151441216468811),
 ('execute', 0.3136429190635681)]

In [28]:
w1 = "unsafe"
model.wv.most_similar(positive=w1)

[('execute', 0.5023025870323181),
 ('stamp_nonce', 0.4940364956855774),
 ('safe', 0.4894552230834961),
 ('sy', 0.48135972023010254),
 ('backticks', 0.4781866669654846),
 ('shell_exec', 0.47183284163475037),
 ('index', 0.4711758494377136),
 ('reads', 0.460822194814682),
 ('balancetags', 0.45632514357566833),
 ('com_categories', 0.4449407458305359)]

In [29]:
w1 = "where"
model.wv.most_similar(positive=w1)

[('flaw', 0.4381900429725647),
 ('tainted', 0.40257951617240906),
 ('query', 0.3612777888774872),
 ('select', 0.32410746812820435),
 ('additionalfrom', 0.2813202440738678),
 ('ent_quotes', 0.23073211312294006),
 ('mysql_user', 0.22824901342391968),
 ('else', 0.2276645302772522),
 ('climits', 0.21416254341602325),
 ('uitype', 0.21273191273212433)]

In [30]:
w1 = ["where", "select", "sql"]
model.wv.most_similar(positive=w1)

[('privmsgs_table', 0.4590402841567993),
 ('users_table', 0.4351050853729248),
 ('privmsgs_id', 0.4340338706970215),
 ('tainted', 0.42911678552627563),
 ('additionalfrom', 0.425476998090744),
 ('pm', 0.41146403551101685),
 ('recordcount', 0.395660400390625),
 ('ip_address', 0.38256192207336426),
 ('user_id', 0.37450289726257324),
 ('customers_id', 0.37283867597579956)]

In [34]:
model.wv["where"]

array([-2.9118001 , -0.95720434,  1.3604698 , -0.4261985 ,  1.0065436 ,
        3.7684412 , -1.3207746 ,  0.4801017 ,  0.7529626 , -1.9404037 ,
       -2.6120505 ,  0.7727567 ,  0.09535431,  3.0041294 ,  1.7900286 ,
       -0.28684667,  1.667999  ,  3.0350075 , -4.0512567 ,  5.3772297 ,
        4.254334  ,  1.9815658 ,  3.2603414 , -2.4737027 , -1.0775232 ,
       -0.12604682, -0.07415418,  0.8458014 , -0.9158774 , -3.5292957 ,
        1.505172  ,  1.8314044 ,  5.6136594 , -0.76995707,  3.889162  ,
        2.1360812 ,  0.6138859 ,  3.1917708 , -3.2246528 , -1.4320898 ,
       -0.18972056,  3.3971999 ,  2.818257  ,  5.7847543 , -0.32451153,
        1.2483342 ,  0.2427151 ,  2.161397  , -3.4310782 , -2.326562  ,
        3.5626423 , -4.519233  ,  0.75486475,  4.1068583 ,  0.58687145,
        1.292275  ,  2.125567  , -0.10269383,  2.012545  ,  1.3324026 ,
        3.549856  , -3.3005083 , -3.5391567 ,  0.269135  ,  1.7144408 ,
       -1.411999  ,  4.7134924 ,  0.26784053, -0.22343299, -1.22

In [35]:
model.wv.vocab

{'php': <gensim.models.keyedvectors.Vocab at 0x1f6b4581c18>,
 'wpseo': <gensim.models.keyedvectors.Vocab at 0x1f6b44f2b00>,
 'plugin': <gensim.models.keyedvectors.Vocab at 0x1f6b44f29e8>,
 'file': <gensim.models.keyedvectors.Vocab at 0x1f6b44f2e48>,
 'package': <gensim.models.keyedvectors.Vocab at 0x1f6b44f2b38>,
 'admin': <gensim.models.keyedvectors.Vocab at 0x1f6b44f2ac8>,
 'bulk': <gensim.models.keyedvectors.Vocab at 0x1f6b44f2cf8>,
 'editor': <gensim.models.keyedvectors.Vocab at 0x1f6b5fe9048>,
 'since': <gensim.models.keyedvectors.Vocab at 0x1f6b5fe9080>,
 'implements': <gensim.models.keyedvectors.Vocab at 0x1f6b5fe90b8>,
 'table': <gensim.models.keyedvectors.Vocab at 0x1f6b5fe90f0>,
 'for': <gensim.models.keyedvectors.Vocab at 0x1f6b5fe9128>,
 'editing': <gensim.models.keyedvectors.Vocab at 0x1f6b5fe9160>,
 'class': <gensim.models.keyedvectors.Vocab at 0x1f6b5fe9198>,
 'extends': <gensim.models.keyedvectors.Vocab at 0x1f6b5fe91d0>,
 'the': <gensim.models.keyedvectors.Vocab at 0x1

In [38]:
#need to iterate over model.wv.vocab dictionary to get all features names
model.wv.vocab.keys()

dict_keys(['php', 'wpseo', 'plugin', 'file', 'package', 'admin', 'bulk', 'editor', 'since', 'implements', 'table', 'for', 'editing', 'class', 'extends', 'the', 'nonce', 'that', 'was', 'passed', 'with', 'request', 'var', 'string', 'private', 'array', 'of', 'post', 'types', 'which', 'current', 'user', 'has', 'capabilities', 'all_posts', 'edit_posts', 'but', 'not', 'saves', 'all', 'metadata', 'into', 'this', 'protected', 'meta_data', 'requested', 'page_url', 'request_url', 'page', 'depending', 'on', 'paged', 'if', 'is', 'page_type', 'else', 'it', 'will', 'be', 'integer', 'current_page', 'filter', 'used', 'current_filter', 'status', 'post_status', 'current_status', 'order', 'and', 'orderby', 'current_order', 'instance', 'example', 'title', 'description', 'based', 'there', 'an', 'url', 'part', 'navigation', 'settings', 'in', 'pagination', 'holds', 'sanitized', 'data', 'from', 'input', 'input_fields', 'constructor', 'param', 'args', 'arguments', 'public', 'function', 'parent', 'wp_parse_args